# Extracting data for review -- MIMIC III

Our goal is to extract drug-AE pairs from the text and the context around them, and form a table with the following fields:

- chunk (context in which the AE and drug occur)
- AE
- Drug
- Vote (to be filled in after reviewing the chunk to see if it's a true drug-AE pair)

The procedure:
1. match against a list of drug keywords. If a drug is identified, extract the chunk of characters drug characters before and after the drug.
2. for each chunk, match against a list of AE. If an AE is identified, save the drug, AE and chunk for further review to see if it's a true drug-AE pair.
3. look at the chunk for trigger words like 'secondary to', 'caused by'. Keep only the chunk with these trigger words.

In [54]:
# IMPORT PACKAGES
import re
import csv
import sys
import pandas as pd

In [55]:
# ***************** #
# import dataset

# read in the .csv file
mimic_notes = pd.read_csv('./MIMIC III/NOTEEVENTS.csv')

C:\hsaauthorised\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2698: DtypeWarning: Columns (4,5) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [56]:
mimic_notes.head()

ROW_ID  SUBJECT_ID   HADM_ID   CHARTDATE CHARTTIME STORETIME  \
0     174       22532  167853.0  2151-08-04       NaN       NaN   
1     175       13702  107527.0  2118-06-14       NaN       NaN   
2     176       13702  167118.0  2119-05-25       NaN       NaN   
3     177       13702  196489.0  2124-08-18       NaN       NaN   
4     178       26880  135453.0  2162-03-25       NaN       NaN   

            CATEGORY DESCRIPTION  CGID  ISERROR  \
0  Discharge summary      Report   NaN      NaN   
1  Discharge summary      Report   NaN      NaN   
2  Discharge summary      Report   NaN      NaN   
3  Discharge summary      Report   NaN      NaN   
4  Discharge summary      Report   NaN      NaN   

                                                TEXT  
0  Admission Date:  [**2151-7-16**]       Dischar...  
1  Admission Date:  [**2118-6-2**]       Discharg...  
2  Admission Date:  [**2119-5-4**]              D...  
3  Admission Date:  [**2124-7-21**]              ...  
4  Admission Date:  [**2162-3-3**]              D...

In [57]:
print(len(mimic_notes))

2083180


In [58]:
# Remove dsumm with less than 2000 characters
charlen_2000 = mimic_notes['TEXT'].map(len)>= 2000
mimic_notes_2000=mimic_notes[charlen_2000]
len(mimic_notes_2000)

477266

In [59]:
# Keep only those where CATEGORY = "Discharge summary"
is_discharge_summ = mimic_notes_2000['CATEGORY']=='Discharge summary'
mimic_notes_dsumm = mimic_notes_2000[is_discharge_summ]
len(mimic_notes_dsumm)

55813

In [60]:
# Select the first 5000 discharge summaries
mimic_notes_final = mimic_notes_dsumm[:5000]
len(mimic_notes_final)

5000

In [61]:
mimic_notes_final.head()

ROW_ID  SUBJECT_ID   HADM_ID   CHARTDATE CHARTTIME STORETIME  \
1     175       13702  107527.0  2118-06-14       NaN       NaN   
2     176       13702  167118.0  2119-05-25       NaN       NaN   
3     177       13702  196489.0  2124-08-18       NaN       NaN   
4     178       26880  135453.0  2162-03-25       NaN       NaN   
5     179       53181  170490.0  2172-03-08       NaN       NaN   

            CATEGORY DESCRIPTION  CGID  ISERROR  \
1  Discharge summary      Report   NaN      NaN   
2  Discharge summary      Report   NaN      NaN   
3  Discharge summary      Report   NaN      NaN   
4  Discharge summary      Report   NaN      NaN   
5  Discharge summary      Report   NaN      NaN   

                                                TEXT  
1  Admission Date:  [**2118-6-2**]       Discharg...  
2  Admission Date:  [**2119-5-4**]              D...  
3  Admission Date:  [**2124-7-21**]              ...  
4  Admission Date:  [**2162-3-3**]              D...  
5  Admission Date:  [**2172-3-5**]              D...

In [69]:
# Save to list

encounter_id = mimic_notes_final['ROW_ID'].tolist()
dsumm_raw = mimic_notes_final['TEXT'].tolist()

print(len(encounter_id), len(dsumm_raw))

5000 5000


In [70]:
# Clean up escape characters
dsumm=[]

for i in dsumm_raw:
    dsumm_curr = i.replace("\n", ' ').replace("\r", ' ')
    dsumm_curr = dsumm_curr.strip().lower()
    dsumm.append(dsumm_curr)

In [71]:
print("number of discharge summaries extracted:",len(dsumm))
unique_ecids=set(encounter_id)
print("number of unique encounter_ids:",len(unique_ecids))

number of discharge summaries extracted: 5000
number of unique encounter_ids: 5000


In [73]:
encounter_id[0:4]

[175, 176, 177, 178]

In [74]:
# view a sample of the data

print(encounter_id[0],'\n', dsumm[0],'\n')

175 
 admission date:  [**2118-6-2**]       discharge date:  [**2118-6-14**]  date of birth:                    sex:  f  service:  micu and then to [**doctor last name **] medicine  history of present illness:  this is an 81-year-old female with a history of emphysema (not on home o2), who presents with three days of shortness of breath thought by her primary care doctor to be a copd flare.  two days prior to admission, she was started on a prednisone taper and one day prior to admission she required oxygen at home in order to maintain oxygen saturation greater than 90%.  she has also been on levofloxacin and nebulizers, and was not getting better, and presented to the [**hospital1 18**] emergency room.  in the [**hospital3 **] emergency room, her oxygen saturation was 100% on cpap.  she was not able to be weaned off of this despite nebulizer treatment and solu-medrol 125 mg iv x2.  review of systems is negative for the following:  fevers, chills, nausea, vomiting, night sweats, change

## 1. match against a list of drug keywords

If a drug is identified, extract the chunk of characters 100 characters before and after the drug.

In [ ]:
import os
os.getcwd()

In [77]:
import pandas as pd
# import drug list
drug_dataframe = pd.read_csv('./drug_dictionary.csv', names = ['a','b','c','d','e','f'])

In [78]:
drug_dataframe[:5]

a          b                 c      d         e               f
0    SN  Item Name        Ingredient  Class      Type  Abbrieviations
1  3263        NaN               NaN    NaN  COSMETIC             NaN
2   161        NaN              ALOE    NaN  COSMETIC             NaN
3  3922        NaN     AQUEOUS CREAM    NaN  COSMETIC             NaN
4  1623        NaN  BENZOYL PEROXIDE    NaN  COSMETIC             NaN

In [79]:
# get the drugs from the third column for drugs
is_drug = drug_dataframe['e']=="DRUG"
drug_dict = drug_dataframe['c'][is_drug].dropna()
print("number of drug names:",len(drug_dict))
print(drug_dict[0:4])

# get the drugs from the fourth column for drug classes
is_drug_class = drug_dataframe['e']=="DRUG CLASS"
drug_class_dict = drug_dataframe['d'][is_drug_class].dropna()
print("number of drug classes:",len(drug_class_dict))
print(drug_class_dict[0:4])

# combine into one list
drug_dict=drug_dict.tolist() + drug_class_dict.tolist()
print("total number of drugs combined:",len(drug_dict))

number of drug names: 6829
36               ABACAVIR
37    ABACAVIR-LAMIVUDINE
38              ABATACEPT
39              ABCIXIMAB
Name: c, dtype: object
number of drug classes: 118
3998       ANTHELMINTICS
3999    ANTICHOLINERGICS
4000       ANTIDIABETICS
4001      ANTI-PARKINSON
Name: d, dtype: object
total number of drugs combined: 6947


In [80]:
# convert to lower case
drug_dict=[drug.lower() for drug in drug_dict]

# add in padding
drug_dict=[" " + drug + " " for drug in drug_dict]

# # remove duplicates
drug_dict=list(dict.fromkeys(drug_dict))
print("final number of drugs combined:", len(drug_dict))

final number of drugs combined: 2680


In [81]:
def searchandextract(txt, target):
    indices = [m.start() for m in re.finditer(target,txt)]
    drug_list = []
    context_list = []
    for i in indices:
        drug = target
        context = txt[i-100:i+len(target)+100]
        drug_list.append(drug)
        context_list.append(context)
    return drug_list, context_list

In [82]:
master_drug_list = []
master_context_list = []
master_ecid_list = []

# store results in master list
for i in range (len(dsumm)):
    print("now looking at encounter_id:",encounter_id[i])
    curr_dsumm=dsumm[i]
    curr_ecid=encounter_id[i]
    for drug in drug_dict:
        drug_list, context_list = searchandextract(curr_dsumm, drug)
        ecid_list=[encounter_id[i]]*len(drug_list)
        master_drug_list=master_drug_list+drug_list
        master_context_list=master_context_list+context_list
        master_ecid_list=master_ecid_list+ecid_list
print("total number of discharge summaries scanned:",len(dsumm))
print("total number of instances of drugs identified:",len(master_drug_list))

now looking at encounter_id: 175
now looking at encounter_id: 176
now looking at encounter_id: 177
now looking at encounter_id: 178
now looking at encounter_id: 179
now looking at encounter_id: 180
now looking at encounter_id: 181
now looking at encounter_id: 182
now looking at encounter_id: 183
now looking at encounter_id: 184
now looking at encounter_id: 185
now looking at encounter_id: 223
now looking at encounter_id: 224
now looking at encounter_id: 225
now looking at encounter_id: 226
now looking at encounter_id: 227
now looking at encounter_id: 228
now looking at encounter_id: 229
now looking at encounter_id: 230
now looking at encounter_id: 231
now looking at encounter_id: 232
now looking at encounter_id: 233
now looking at encounter_id: 234
now looking at encounter_id: 235
now looking at encounter_id: 236
now looking at encounter_id: 237
now looking at encounter_id: 238
now looking at encounter_id: 239
now looking at encounter_id: 240
now looking at encounter_id: 241
now lookin

now looking at encounter_id: 448
now looking at encounter_id: 449
now looking at encounter_id: 450
now looking at encounter_id: 451
now looking at encounter_id: 452
now looking at encounter_id: 529
now looking at encounter_id: 530
now looking at encounter_id: 531
now looking at encounter_id: 532
now looking at encounter_id: 533
now looking at encounter_id: 534
now looking at encounter_id: 535
now looking at encounter_id: 536
now looking at encounter_id: 537
now looking at encounter_id: 538
now looking at encounter_id: 539
now looking at encounter_id: 540
now looking at encounter_id: 541
now looking at encounter_id: 542
now looking at encounter_id: 543
now looking at encounter_id: 544
now looking at encounter_id: 545
now looking at encounter_id: 546
now looking at encounter_id: 547
now looking at encounter_id: 548
now looking at encounter_id: 549
now looking at encounter_id: 550
now looking at encounter_id: 551
now looking at encounter_id: 552
now looking at encounter_id: 553
now lookin

now looking at encounter_id: 519
now looking at encounter_id: 520
now looking at encounter_id: 521
now looking at encounter_id: 522
now looking at encounter_id: 523
now looking at encounter_id: 525
now looking at encounter_id: 526
now looking at encounter_id: 527
now looking at encounter_id: 275
now looking at encounter_id: 276
now looking at encounter_id: 277
now looking at encounter_id: 279
now looking at encounter_id: 280
now looking at encounter_id: 281
now looking at encounter_id: 282
now looking at encounter_id: 283
now looking at encounter_id: 284
now looking at encounter_id: 285
now looking at encounter_id: 286
now looking at encounter_id: 287
now looking at encounter_id: 288
now looking at encounter_id: 289
now looking at encounter_id: 290
now looking at encounter_id: 291
now looking at encounter_id: 292
now looking at encounter_id: 293
now looking at encounter_id: 294
now looking at encounter_id: 295
now looking at encounter_id: 296
now looking at encounter_id: 297
now lookin

now looking at encounter_id: 1050
now looking at encounter_id: 1051
now looking at encounter_id: 1052
now looking at encounter_id: 1053
now looking at encounter_id: 1054
now looking at encounter_id: 1055
now looking at encounter_id: 1056
now looking at encounter_id: 1057
now looking at encounter_id: 1058
now looking at encounter_id: 1059
now looking at encounter_id: 1060
now looking at encounter_id: 1061
now looking at encounter_id: 1062
now looking at encounter_id: 1063
now looking at encounter_id: 1064
now looking at encounter_id: 1065
now looking at encounter_id: 1066
now looking at encounter_id: 1067
now looking at encounter_id: 1068
now looking at encounter_id: 1069
now looking at encounter_id: 1070
now looking at encounter_id: 768
now looking at encounter_id: 769
now looking at encounter_id: 770
now looking at encounter_id: 771
now looking at encounter_id: 772
now looking at encounter_id: 773
now looking at encounter_id: 774
now looking at encounter_id: 781
now looking at encount

now looking at encounter_id: 1180
now looking at encounter_id: 1181
now looking at encounter_id: 1182
now looking at encounter_id: 1183
now looking at encounter_id: 1184
now looking at encounter_id: 1185
now looking at encounter_id: 1186
now looking at encounter_id: 1187
now looking at encounter_id: 1188
now looking at encounter_id: 1189
now looking at encounter_id: 1190
now looking at encounter_id: 1191
now looking at encounter_id: 1192
now looking at encounter_id: 1193
now looking at encounter_id: 1194
now looking at encounter_id: 1195
now looking at encounter_id: 1196
now looking at encounter_id: 1197
now looking at encounter_id: 1198
now looking at encounter_id: 1199
now looking at encounter_id: 1200
now looking at encounter_id: 1201
now looking at encounter_id: 1202
now looking at encounter_id: 1203
now looking at encounter_id: 1204
now looking at encounter_id: 1378
now looking at encounter_id: 1379
now looking at encounter_id: 1380
now looking at encounter_id: 1381
now looking at

...

now looking at encounter_id: 3619
now looking at encounter_id: 3620
now looking at encounter_id: 3621
now looking at encounter_id: 3622
now looking at encounter_id: 3623
now looking at encounter_id: 3624
now looking at encounter_id: 3625
now looking at encounter_id: 3626
now looking at encounter_id: 3627
now looking at encounter_id: 3628
now looking at encounter_id: 3629
now looking at encounter_id: 3829
now looking at encounter_id: 3830
now looking at encounter_id: 3831
now looking at encounter_id: 3832
now looking at encounter_id: 3833
now looking at encounter_id: 3834
now looking at encounter_id: 3835
now looking at encounter_id: 3836
now looking at encounter_id: 3837
now looking at encounter_id: 3838
now looking at encounter_id: 3839
now looking at encounter_id: 3840
now looking at encounter_id: 3841
now looking at encounter_id: 3842
now looking at encounter_id: 3843
now looking at encounter_id: 3844
now looking at encounter_id: 3845
now looking at encounter_id: 3846
now looking at

now looking at encounter_id: 4383
now looking at encounter_id: 4384
now looking at encounter_id: 4385
now looking at encounter_id: 4386
now looking at encounter_id: 4438
now looking at encounter_id: 4439
now looking at encounter_id: 4440
now looking at encounter_id: 4441
now looking at encounter_id: 4442
now looking at encounter_id: 4443
now looking at encounter_id: 4444
now looking at encounter_id: 4445
now looking at encounter_id: 4446
now looking at encounter_id: 4521
now looking at encounter_id: 4522
now looking at encounter_id: 4523
now looking at encounter_id: 4524
now looking at encounter_id: 4525
now looking at encounter_id: 4526
now looking at encounter_id: 4527
now looking at encounter_id: 4528
now looking at encounter_id: 4529
now looking at encounter_id: 4530
now looking at encounter_id: 4531
now looking at encounter_id: 4532
now looking at encounter_id: 4533
now looking at encounter_id: 4534
now looking at encounter_id: 4535
now looking at encounter_id: 4536
now looking at

now looking at encounter_id: 4507
now looking at encounter_id: 4508
now looking at encounter_id: 4509
now looking at encounter_id: 4510
now looking at encounter_id: 4511
now looking at encounter_id: 4512
now looking at encounter_id: 4513
now looking at encounter_id: 4514
now looking at encounter_id: 4515
now looking at encounter_id: 4516
now looking at encounter_id: 4517
now looking at encounter_id: 4518
now looking at encounter_id: 4519
now looking at encounter_id: 4520
now looking at encounter_id: 4151
now looking at encounter_id: 4152
now looking at encounter_id: 4153
now looking at encounter_id: 4154
now looking at encounter_id: 4155
now looking at encounter_id: 4156
now looking at encounter_id: 4157
now looking at encounter_id: 4158
now looking at encounter_id: 4159
now looking at encounter_id: 4160
now looking at encounter_id: 4161
now looking at encounter_id: 4162
now looking at encounter_id: 4163
now looking at encounter_id: 4164
now looking at encounter_id: 4165
now looking at

now looking at encounter_id: 4597
now looking at encounter_id: 4598
now looking at encounter_id: 4702
now looking at encounter_id: 4703
now looking at encounter_id: 4704
now looking at encounter_id: 4705
now looking at encounter_id: 4706
now looking at encounter_id: 4707
now looking at encounter_id: 4708
now looking at encounter_id: 4709
now looking at encounter_id: 4710
now looking at encounter_id: 4711
now looking at encounter_id: 4712
now looking at encounter_id: 4713
now looking at encounter_id: 4714
now looking at encounter_id: 4715
now looking at encounter_id: 4716
now looking at encounter_id: 4718
now looking at encounter_id: 4719
now looking at encounter_id: 4720
now looking at encounter_id: 4721
now looking at encounter_id: 4722
now looking at encounter_id: 4723
now looking at encounter_id: 4724
now looking at encounter_id: 4725
now looking at encounter_id: 4726
now looking at encounter_id: 4727
now looking at encounter_id: 4728
now looking at encounter_id: 4729
now looking at

now looking at encounter_id: 5157
now looking at encounter_id: 5158
now looking at encounter_id: 5159
now looking at encounter_id: 5160
now looking at encounter_id: 5161
now looking at encounter_id: 4940
now looking at encounter_id: 4941
now looking at encounter_id: 4942
now looking at encounter_id: 4943
now looking at encounter_id: 4944
now looking at encounter_id: 4945
now looking at encounter_id: 4946
now looking at encounter_id: 4947
now looking at encounter_id: 4948
now looking at encounter_id: 4949
now looking at encounter_id: 4950
now looking at encounter_id: 4951
now looking at encounter_id: 4952
now looking at encounter_id: 4953
now looking at encounter_id: 4954
now looking at encounter_id: 4955
now looking at encounter_id: 4956
now looking at encounter_id: 4957
now looking at encounter_id: 4958
now looking at encounter_id: 4959
now looking at encounter_id: 4960
now looking at encounter_id: 4961
now looking at encounter_id: 4962
now looking at encounter_id: 4963
now looking at

In [83]:
master_drug_list[:5]

[' aspirin ', ' aspirin ', ' citalopram ', ' diltiazem ', ' diltiazem ']

In [84]:
master_context_list[:5]

['. pulmicort nebulizer b.i.d. 7. albuterol nebulizer q.4. prn. 8. lexapro 10 mg q.d. 9. protonix 40 mg q.d. 10. aspirin 81 mg q.d.  allergies:  norvasc leads to lightheadedness and headache.  family history:  noncontributory.  soc',
 'cal rehabilitation.  discharge medications: 1. levothyroxine 75 mcg p.o. q.d. 2. citalopram 10 mg p.o. q.d. 3. aspirin 81 mg p.o. q.d. 4. fluticasone 110 mcg two puffs inhaled b.i.d. 5. salmeterol diskus one inhalation b.i.d. 6. ',
 '] for both pulmonary and physical rehabilitation.  discharge medications: 1. levothyroxine 75 mcg p.o. q.d. 2. citalopram 10 mg p.o. q.d. 3. aspirin 81 mg p.o. q.d. 4. fluticasone 110 mcg two puffs inhaled b.i.d. 5. salmeterol disku',
 'd no evidence of ekg changes and negative troponin, negative cks x3.  she was continued on aspirin, imdur, and diltiazem for rate control per her outpatient regimen.  3. hypertension:  she was maintained on diltiazem and hydrochlor',
 'in, imdur, and diltiazem for rate control per her outpati

In [85]:
master_ecid_list[:5]

[175, 175, 175, 175, 175]

In [86]:
interim_dataframe = pd.DataFrame(data={'encounter_id':master_ecid_list,'context':master_context_list, 'drug':master_drug_list})

In [87]:
# ***************** #
interim_dataframe.to_csv('./interim_MIMIC.csv', sep ='|')

## 2. for each chunk, match against a list of AEs.

In [88]:
# import the list of aes
ae_dict = []
e=open("./ae_list.txt","r")
for x in e:
    ae_dict.append(" "+x.strip()+" ")

In [89]:
# now we have a list of AEs and their context, search for drugs in the context
# initiate drug, ae and context list
aes = []
drugs = []
contexts = []
encounter_ids = []

In [90]:
# add the ae, drug if they exist in the context

for i in range (len(master_drug_list)):
    print('parsing through item ' + str(i) + ' out of ' + str(len(master_drug_list)-1)) 
    for j in range (len(ae_dict)):
        # if the ae exists in the context surrounding the drug:
        if (ae_dict[j] in master_context_list[i]):
            drug = master_drug_list[i]
            ae = ae_dict[j]
            context = master_context_list[i]
            ecid= master_ecid_list[i]
            aes.append(ae)
            drugs.append(drug)
            contexts.append(context)
            encounter_ids.append(ecid)

parsing through item 0 out of 97442
parsing through item 1 out of 97442
parsing through item 2 out of 97442
parsing through item 3 out of 97442
parsing through item 4 out of 97442
parsing through item 5 out of 97442
parsing through item 6 out of 97442
parsing through item 7 out of 97442
parsing through item 8 out of 97442
parsing through item 9 out of 97442
parsing through item 10 out of 97442
parsing through item 11 out of 97442
parsing through item 12 out of 97442
parsing through item 13 out of 97442
parsing through item 14 out of 97442
parsing through item 15 out of 97442
parsing through item 16 out of 97442
parsing through item 17 out of 97442
parsing through item 18 out of 97442
parsing through item 19 out of 97442
parsing through item 20 out of 97442
parsing through item 21 out of 97442
parsing through item 22 out of 97442
parsing through item 23 out of 97442
parsing through item 24 out of 97442
parsing through item 25 out of 97442
parsing through item 26 out of 97442
parsing thr

parsing through item 224 out of 97442
parsing through item 225 out of 97442
parsing through item 226 out of 97442
parsing through item 227 out of 97442
parsing through item 228 out of 97442
parsing through item 229 out of 97442
parsing through item 230 out of 97442
parsing through item 231 out of 97442
parsing through item 232 out of 97442
parsing through item 233 out of 97442
parsing through item 234 out of 97442
parsing through item 235 out of 97442
parsing through item 236 out of 97442
parsing through item 237 out of 97442
parsing through item 238 out of 97442
parsing through item 239 out of 97442
parsing through item 240 out of 97442
parsing through item 241 out of 97442
parsing through item 242 out of 97442
parsing through item 243 out of 97442
parsing through item 244 out of 97442
parsing through item 245 out of 97442
parsing through item 246 out of 97442
parsing through item 247 out of 97442
parsing through item 248 out of 97442
parsing through item 249 out of 97442
parsing thro

parsing through item 442 out of 97442
parsing through item 443 out of 97442
parsing through item 444 out of 97442
parsing through item 445 out of 97442
parsing through item 446 out of 97442
parsing through item 447 out of 97442
parsing through item 448 out of 97442
parsing through item 449 out of 97442
parsing through item 450 out of 97442
parsing through item 451 out of 97442
parsing through item 452 out of 97442
parsing through item 453 out of 97442
parsing through item 454 out of 97442
parsing through item 455 out of 97442
parsing through item 456 out of 97442
parsing through item 457 out of 97442
parsing through item 458 out of 97442
parsing through item 459 out of 97442
parsing through item 460 out of 97442
parsing through item 461 out of 97442
parsing through item 462 out of 97442
parsing through item 463 out of 97442
parsing through item 464 out of 97442
parsing through item 465 out of 97442
parsing through item 466 out of 97442
parsing through item 467 out of 97442
parsing thro

parsing through item 664 out of 97442
parsing through item 665 out of 97442
parsing through item 666 out of 97442
parsing through item 667 out of 97442
parsing through item 668 out of 97442
parsing through item 669 out of 97442
parsing through item 670 out of 97442
parsing through item 671 out of 97442
parsing through item 672 out of 97442
parsing through item 673 out of 97442
parsing through item 674 out of 97442
parsing through item 675 out of 97442
parsing through item 676 out of 97442
parsing through item 677 out of 97442
parsing through item 678 out of 97442
parsing through item 679 out of 97442
parsing through item 680 out of 97442
parsing through item 681 out of 97442
parsing through item 682 out of 97442
parsing through item 683 out of 97442
parsing through item 684 out of 97442
parsing through item 685 out of 97442
parsing through item 686 out of 97442
parsing through item 687 out of 97442
parsing through item 688 out of 97442
parsing through item 689 out of 97442
parsing thro

parsing through item 880 out of 97442
parsing through item 881 out of 97442
parsing through item 882 out of 97442
parsing through item 883 out of 97442
parsing through item 884 out of 97442
parsing through item 885 out of 97442
parsing through item 886 out of 97442
parsing through item 887 out of 97442
parsing through item 888 out of 97442
parsing through item 889 out of 97442
parsing through item 890 out of 97442
parsing through item 891 out of 97442
parsing through item 892 out of 97442
parsing through item 893 out of 97442
parsing through item 894 out of 97442
parsing through item 895 out of 97442
parsing through item 896 out of 97442
parsing through item 897 out of 97442
parsing through item 898 out of 97442
parsing through item 899 out of 97442
parsing through item 900 out of 97442
parsing through item 901 out of 97442
parsing through item 902 out of 97442
parsing through item 903 out of 97442
parsing through item 904 out of 97442
parsing through item 905 out of 97442
parsing thro

...

parsing through item 96477 out of 97442
parsing through item 96478 out of 97442
parsing through item 96479 out of 97442
parsing through item 96480 out of 97442
parsing through item 96481 out of 97442
parsing through item 96482 out of 97442
parsing through item 96483 out of 97442
parsing through item 96484 out of 97442
parsing through item 96485 out of 97442
parsing through item 96486 out of 97442
parsing through item 96487 out of 97442
parsing through item 96488 out of 97442
parsing through item 96489 out of 97442
parsing through item 96490 out of 97442
parsing through item 96491 out of 97442
parsing through item 96492 out of 97442
parsing through item 96493 out of 97442
parsing through item 96494 out of 97442
parsing through item 96495 out of 97442
parsing through item 96496 out of 97442
parsing through item 96497 out of 97442
parsing through item 96498 out of 97442
parsing through item 96499 out of 97442
parsing through item 96500 out of 97442
parsing through item 96501 out of 97442


parsing through item 96686 out of 97442
parsing through item 96687 out of 97442
parsing through item 96688 out of 97442
parsing through item 96689 out of 97442
parsing through item 96690 out of 97442
parsing through item 96691 out of 97442
parsing through item 96692 out of 97442
parsing through item 96693 out of 97442
parsing through item 96694 out of 97442
parsing through item 96695 out of 97442
parsing through item 96696 out of 97442
parsing through item 96697 out of 97442
parsing through item 96698 out of 97442
parsing through item 96699 out of 97442
parsing through item 96700 out of 97442
parsing through item 96701 out of 97442
parsing through item 96702 out of 97442
parsing through item 96703 out of 97442
parsing through item 96704 out of 97442
parsing through item 96705 out of 97442
parsing through item 96706 out of 97442
parsing through item 96707 out of 97442
parsing through item 96708 out of 97442
parsing through item 96709 out of 97442
parsing through item 96710 out of 97442


parsing through item 96899 out of 97442
parsing through item 96900 out of 97442
parsing through item 96901 out of 97442
parsing through item 96902 out of 97442
parsing through item 96903 out of 97442
parsing through item 96904 out of 97442
parsing through item 96905 out of 97442
parsing through item 96906 out of 97442
parsing through item 96907 out of 97442
parsing through item 96908 out of 97442
parsing through item 96909 out of 97442
parsing through item 96910 out of 97442
parsing through item 96911 out of 97442
parsing through item 96912 out of 97442
parsing through item 96913 out of 97442
parsing through item 96914 out of 97442
parsing through item 96915 out of 97442
parsing through item 96916 out of 97442
parsing through item 96917 out of 97442
parsing through item 96918 out of 97442
parsing through item 96919 out of 97442
parsing through item 96920 out of 97442
parsing through item 96921 out of 97442
parsing through item 96922 out of 97442
parsing through item 96923 out of 97442


parsing through item 97105 out of 97442
parsing through item 97106 out of 97442
parsing through item 97107 out of 97442
parsing through item 97108 out of 97442
parsing through item 97109 out of 97442
parsing through item 97110 out of 97442
parsing through item 97111 out of 97442
parsing through item 97112 out of 97442
parsing through item 97113 out of 97442
parsing through item 97114 out of 97442
parsing through item 97115 out of 97442
parsing through item 97116 out of 97442
parsing through item 97117 out of 97442
parsing through item 97118 out of 97442
parsing through item 97119 out of 97442
parsing through item 97120 out of 97442
parsing through item 97121 out of 97442
parsing through item 97122 out of 97442
parsing through item 97123 out of 97442
parsing through item 97124 out of 97442
parsing through item 97125 out of 97442
parsing through item 97126 out of 97442
parsing through item 97127 out of 97442
parsing through item 97128 out of 97442
parsing through item 97129 out of 97442


parsing through item 97311 out of 97442
parsing through item 97312 out of 97442
parsing through item 97313 out of 97442
parsing through item 97314 out of 97442
parsing through item 97315 out of 97442
parsing through item 97316 out of 97442
parsing through item 97317 out of 97442
parsing through item 97318 out of 97442
parsing through item 97319 out of 97442
parsing through item 97320 out of 97442
parsing through item 97321 out of 97442
parsing through item 97322 out of 97442
parsing through item 97323 out of 97442
parsing through item 97324 out of 97442
parsing through item 97325 out of 97442
parsing through item 97326 out of 97442
parsing through item 97327 out of 97442
parsing through item 97328 out of 97442
parsing through item 97329 out of 97442
parsing through item 97330 out of 97442
parsing through item 97331 out of 97442
parsing through item 97332 out of 97442
parsing through item 97333 out of 97442
parsing through item 97334 out of 97442
parsing through item 97335 out of 97442


## 3. match against a list of trigger phrases

In [108]:
# import the list of trigger words
trigger_list = []
f=open("./triggerphrases.txt","r")
for x in f:
    trigger_list.append(" "+x.strip()+" ")

In [109]:
print(trigger_list)

[' 2 to ', ' adr ', ' adrs ', ' adverse ', ' adverse drug reaction ', ' adverse effect ', ' adverse event ', ' adverse reaction ', ' ae ', ' aes ', ' after ', ' after starting ', ' after taking ', ' associate ', ' associated ', ' associates ', ' attribute ', ' attributed ', ' attributes ', ' attributing ', ' because ', ' because of ', ' cause ', ' caused ', ' causes ', ' causing ', ' cease ', ' ceased ', ' ceases ', ' cessation of ', ' change to ', ' changed to ', ' changes to ', ' changing ', ' control with ', ' controlled with ', ' controlling ', ' controls with ', ' convert ', ' converted to ', ' converting ', ' converts ', ' DC ', ' decr dose ', ' decr doses ', ' decrease ', ' decreased ', ' decreases ', ' decreasing ', ' develop ', ' develop from ', ' developed ', ' developed from ', ' developing ', ' develops ', ' discontinue ', ' discontinued ', ' discontinues ', ' discontinuing ', ' drug induced ', ' drug reaction ', ' drug related ', ' drug-induced ', ' drug-related ', ' due '

In [110]:
trigger_phrases_contained=[]
count_trigger_phrases=[]

for i in range(len(contexts)):
    trigger_phrase_curr=[]
    count_curr=0
    for j in range(len(trigger_list)):
        if trigger_list[j] in contexts[i]:
            trigger_phrase_curr.append(trigger_list[j])
            count_curr+=1
    trigger_phrases_contained.append(trigger_phrase_curr)
    count_trigger_phrases.append(count_curr)
            

In [111]:
print(len(trigger_phrases_contained))
print(len(count_trigger_phrases))

39684
39684


In [112]:
drug_ae_dataframe = pd.DataFrame(data={'encounter_id':encounter_ids,'ae':aes, 'drug':drugs, 'context':contexts,'trigger_words':trigger_phrases_contained,'trigger_word_count':count_trigger_phrases})

In [113]:
drug_ae_dataframe.head()

encounter_id                 ae                   drug  \
0           175   lightheadedness                aspirin    
1           175          pressure              diltiazem    
2           175          pressure    hydrochlorothiazide    
3           175         dysphagia              lorazepam    
4           176          swelling                heparin    

                                             context   trigger_words  \
0  . pulmicort nebulizer b.i.d. 7. albuterol nebu...              []   
1  in, imdur, and diltiazem for rate control per ...              []   
2   diltiazem for rate control per her outpatient...              []   
3  aine 5 ml p.o. b.i.d. prn, not to be given aro...     [ induced ]   
4  lasix 20mg iv qd. [**5-15**]- rue redness and ...  [ changed to ]   

   trigger_word_count  
0                   0  
1                   0  
2                   0  
3                   1  
4                   1

In [114]:
# keep only those with trigger_phrases
drug_ae_dataframe=drug_ae_dataframe[drug_ae_dataframe['trigger_word_count']>0]

## 4. Removing duplicates and sampling

In [115]:
# remove duplicates
drug_ae_dataframe = drug_ae_dataframe.drop_duplicates(subset='context', keep = 'last')

In [116]:
len(drug_ae_dataframe)

8715

In [117]:
drug_ae_dataframe.head()

encounter_id            ae         drug  \
3            175    dysphagia    lorazepam    
6            176          dvt      heparin    
15           177     weakness      aspirin    
17           177     bleeding      aspirin    
18           177   discomfort      aspirin    

                                              context  \
3   aine 5 ml p.o. b.i.d. prn, not to be given aro...   
6   lasix 20mg iv qd. [**5-15**]- rue redness and ...   
15  eeding throughout the patient's hospitalizatio...   
17  . . # cad: history of lad and rca stenosis on ...   
18  nstipation can use morphine to alleviate sympt...   

                       trigger_words  trigger_word_count  
3                        [ induced ]                   1  
6                     [ changed to ]                   1  
15                      [ switched ]                   1  
17                 [ due ,  due to ]                   2  
18  [ decrease ,  increase ,  stop ]                   3

In [123]:
drug_ae_dataframe=drug_ae_dataframe.groupby("encounter_id").apply(lambda group_df: group_df.sample(n=1, random_state=1)).reset_index(drop=True)

In [124]:
len(drug_ae_dataframe)

3086

In [125]:
len(set(drug_ae_dataframe['encounter_id']))

3086

In [126]:
# ***************** SAVE DATAFRAME #
drug_ae_dataframe.to_csv('./MIMIC-sample_1_per_note.csv')